#Corpus Generator
Generates a corpus for training using the titles of CamHarvestCollection

In [2]:
import pymongo
from pymongo import MongoClient
import nltk
from nltk.corpus import stopwords
import string
import codecs
import gensim 
from gensim import corpora, models
punct_filter = dict((ord(char), u' ') for char in '"#$%&\'()*+,./-:;<=>?@[\\]^_`{|}')   
stop = stopwords.words('english')
mongo_url = 'mongodb://localhost:6666/'
db = 'Cherry'
coll_in = 'Cranberry'
client = MongoClient(mongo_url)
ch = client[db][coll_in]
#corpusfile = 'corpus2.txt' 


In [3]:
def raw_corpus_generator():
    ind = 0 
    with codecs.open('raw_corpus.txt','a',encoding='utf8') as f:
        for rec in ch.find({'crossref_doi':True}):
            lt = rec['title'].lower()
            slt = lt.strip()
            tslt = slt.translate(punct_filter)
            export = tslt+u'\n'
            f.write(export)
            ind+=1
            if ind%100000==0:
                print(ind)

def sanitise(title):
    lt = title.lower()
    slt = lt.strip()
    tslt = slt.translate(punct_filter)
    stop_filtered = [i for i in tslt.split() if i not in stop]
    export = u' '.join(stop_filtered)+u'\n'
    return export

def create_stopword_filtered_corpus():
    ind = 0 
    with codecs.open('second_corpus.txt','a',encoding='utf8') as f:
        for rec in ch.find({'crossref_doi':True}):
            f.write(sanitise(rec['title']))
            ind+=1
            if ind%10000==0:
                print(ind)

In [4]:
class GensimCorpus(object):
    def __init__(self,corpus_text_file,diction):
        self.corpus_text_file = corpus_text_file
        self.dictionary = diction
        
    def __iter__(self):
        for line in open(self.corpus_text_file):
            yield self.dictionary.doc2bow(line.split())

def dictionary_generator(corpus_file):
    dictionary = corpora.Dictionary(line.split() for line in open(corpus_file))
    return dictionary

In [5]:
#dictionary = dictionary_generator('second_corpus.txt')
dictionary = corpora.Dictionary.load('second_dictionary')
corp = GensimCorpus('second_corpus.txt',dictionary)
tfidf = models.TfidfModel(corp)
tfidf_corp = tfidf[corp]
#tfidf.save('second_tfidf')

In [6]:
def tfidf_filtered_corpus_generator(threshold):
    corpus_filename = 'tfidf_filtered_'+str(threshold).strip('.')+'.txt'
    ind=0
    with codecs.open(corpus_filename,'a',encoding='utf8') as f:
        for doc in tfidf_corp:
            if ind%500000 == 0:
                print(ind)
            f.write(' '.join([dictionary[i] for i,j in doc if j>=threshold]))
            f.write('\n')
            ind+=1

In [ ]:
samples = [0.05,0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8]
for samp in samples:
    tfidf_filtered_corpus_generator(samp)
    print('corpus generated')

[(0, 0.408955451739111), (1, 0.9125543482406183)]
0
[(0, 0.3960981035792216), (2, 0.9182081966204311)]
0
[(0, 0.36593824771453237), (3, 0.9306391346056846)]
0
[(0, 0.32380998350713625), (4, 0.9461221351290267)]
0
[(0, 0.49350880336613573), (5, 0.869740801043693)]
0
[(0, 0.16518065242716506), (6, 0.41105040646626073), (7, 0.8965226798066283)]
0
[(0, 0.45559777171903915), (8, 0.4432343802447605), (9, 0.20221568312578003), (10, 0.24265219294794624), (11, 0.3634702839056992), (12, 0.2761948964605731), (13, 0.32315988616774355), (14, 0.4282243631414625)]
0
[(0, 0.21203652326111946), (15, 0.9772617422181923)]
0
[(0, 0.15853695720677646), (6, 0.3945176371579251), (16, 0.9051087598575899)]
0
[(0, 0.1988882771069347), (6, 0.4949314943663158), (17, 0.47519343123311003), (18, 0.5824871166364552), (19, 0.387796636111265)]
0
[(0, 0.2773353349279467), (20, 0.9607731844719666)]
0
[(0, 0.30205024150994186), (21, 0.9532920075211927)]
0
[(0, 0.23799318923326684), (22, 0.9712668232152164)]
0
[(0, 0.23138

In [19]:
'.   '.strip('.')

'   '

In [1]:
ind = 0
for doc in tfidf_corp:
    if ind%100000 == 0:
        ind+=1
        print(doc)
        print(ind)

NameError: name 'tfidf_corp' is not defined